In [13]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/dry-eye-disease/Dry_Eye_Dataset.csv


In [14]:
df=pd.read_csv("/kaggle/input/dry-eye-disease/Dry_Eye_Dataset.csv")
df.head(4)

Gender  Age  Sleep duration  Sleep quality  Stress level Blood pressure  \
0      F   24             9.5              2             1         137/89   
1      M   39             9.6              2             3         108/64   
2      F   45             5.4              1             5         134/81   
3      F   45             5.4              4             5         110/90   

   Heart rate  Daily steps  Physical activity  Height  ...  Smoking  \
0          67         3000                 31     161  ...        N   
1          60        12000                 74     164  ...        N   
2          95        12000                 93     179  ...        N   
3          78        19000                 32     160  ...        N   

  Medical issue Ongoing medication Smart device before bed  \
0             Y                  Y                       N   
1             Y                  Y                       N   
2             N                  N                       Y   
3             Y                  N                       N   

  Average screen time Blue-light filter Discomfort Eye-strain Redness in eye  \
0                 8.7                 N                     Y              Y   
1                 9.6                 Y                     N              N   
2                 4.0                 N                     Y              N   
3                 7.6                 N                     Y              N   

  Itchiness/Irritation in eye Dry Eye Disease  
0                           N               Y  
1                           Y               Y  
2                           N               N  
3                           Y               N  

[4 rows x 26 columns]

In [15]:
df.info()
df=pd.get_dummies(df,columns=["Gender","Sleep disorder","Wake up during night","Caffeine consumption","Alcohol consumption","Smoking", "Medical issue","Ongoing medication","Smart device before bed","Feel sleepy during day" , "Blue-light filter","Discomfort Eye-strain","Redness in eye" , "Itchiness/Irritation in eye","Dry Eye Disease"],drop_first=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20000 entries, 0 to 19999
Data columns (total 26 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   Gender                       20000 non-null  object 
 1   Age                          20000 non-null  int64  
 2   Sleep duration               20000 non-null  float64
 3   Sleep quality                20000 non-null  int64  
 4   Stress level                 20000 non-null  int64  
 5   Blood pressure               20000 non-null  object 
 6   Heart rate                   20000 non-null  int64  
 7   Daily steps                  20000 non-null  int64  
 8   Physical activity            20000 non-null  int64  
 9   Height                       20000 non-null  int64  
 10  Weight                       20000 non-null  int64  
 11  Sleep disorder               20000 non-null  object 
 12  Wake up during night         20000 non-null  object 
 13  Feel sleepy duri

In [16]:
from sklearn.tree import DecisionTreeClassifier,export_graphviz
import graphviz
from sklearn.model_selection import train_test_split

In [17]:
df[["Systolic", "Diastolic"]] = df["Blood pressure"].str.split("/", expand=True).astype(float)
df=df.drop(["Blood pressure"], axis=1)

df = df.astype(float)
df.head(5)

Age  Sleep duration  Sleep quality  Stress level  Heart rate  Daily steps  \
0  24.0             9.5            2.0           1.0        67.0       3000.0   
1  39.0             9.6            2.0           3.0        60.0      12000.0   
2  45.0             5.4            1.0           5.0        95.0      12000.0   
3  45.0             5.4            4.0           5.0        78.0      19000.0   
4  42.0             5.7            3.0           2.0        72.0       4000.0   

   Physical activity  Height  Weight  Average screen time  ...  \
0               31.0   161.0    69.0                  8.7  ...   
1               74.0   164.0    87.0                  9.6  ...   
2               93.0   179.0    94.0                  4.0  ...   
3               32.0   160.0    77.0                  7.6  ...   
4              173.0   179.0    99.0                  3.5  ...   

   Ongoing medication_Y  Smart device before bed_Y  Feel sleepy during day_Y  \
0                   1.0                        0.0                       0.0   
1                   1.0                        0.0                       0.0   
2                   0.0                        1.0                       0.0   
3                   0.0                        0.0                       0.0   
4                   0.0                        0.0                       0.0   

   Blue-light filter_Y  Discomfort Eye-strain_Y  Redness in eye_Y  \
0                  0.0                      1.0               1.0   
1                  1.0                      0.0               0.0   
2                  0.0                      1.0               0.0   
3                  0.0                      1.0               0.0   
4                  0.0                      1.0               1.0   

   Itchiness/Irritation in eye_Y  Dry Eye Disease_Y  Systolic  Diastolic  
0                            0.0                1.0     137.0       89.0  
1                            1.0                1.0     108.0       64.0  
2                            0.0                0.0     134.0       81.0  
3                            1.0                0.0     110.0       90.0  
4                            0.0                1.0      99.0       67.0  

[5 rows x 27 columns]

In [18]:
y=df["Dry Eye Disease_Y"]
x=df.drop("Dry Eye Disease_Y",axis=1)


In [31]:
from pycaret.regression import *

clf1 = setup(df, target = 'Stress level', session_id=123, log_experiment=True, experiment_name='juice1')
best_model = compare_models()

ImportError: cannot import name '_fit_context' from 'sklearn.base' (/usr/local/lib/python3.10/dist-packages/sklearn/base.py)

In [19]:
tree = DecisionTreeClassifier()
model = tree.fit(x,y)
model.score(x,y)
dot=export_graphviz(model,feature_names=x.columns,filled=True)
gorsel=graphviz.Source(dot)
gorsel
#OverFitting

In [20]:
x_train,x_test,y_train,y_test=train_test_split(x,y,random_state=26,train_size=0.76)

In [21]:
#Decision Tree Classification
tree = DecisionTreeClassifier()
model = tree.fit(x_train,y_train)
model.score(x_test,y_test)


0.5808333333333333

In [22]:
#Random Forest Classification
from sklearn.ensemble import RandomForestClassifier
forest= RandomForestClassifier( n_estimators=400, max_depth=30,)
model=forest.fit(x_train,y_train)
model.score(x_test,y_test)


0.6954166666666667

In [23]:
# if you want try model.predic([[x values]])